## Install dependencies

In [1]:
### !pip install mplot3d-dragger
# !pip install pythreejs
# !pip install plotly==4.0.0
#!pip install chart-studio
#!pip install fbprophet

## Import libraries

In [2]:
%matplotlib inline


import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)


#from mpl_toolkits import mplot3d

import plotly.express as px

import matplotlib.pyplot as plt
from matplotlib.pyplot import figure


from IPython.display import display
from ipywidgets import HTML, Text, Output, VBox
from traitlets import link, dlink

import plotly.graph_objects as go
import plotly.express as px


from scipy.spatial import distance
from fbprophet import Prophet

import numpy as np
from numpy.linalg import eig, inv



import warnings
warnings.filterwarnings("ignore")

import datetime
import time 




import numpy as np
import pandas as pd
import scipy

import fbprophet


import warnings
import itertools
import pandas as pd
import numpy as np
import statsmodels.api as sm
import matplotlib.pyplot as plt
plt.style.use('fivethirtyeight')
warnings.filterwarnings("ignore")

## Files

In [3]:
#PATH = '/kaggle/input/idao2020/'


PATH = '.'
import os
for dirname, _, filenames in os.walk(PATH):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.

.\element.py
.\ellipsoid_fit.py
.\errors_denis.xlsx
.\get_calibration_ellipsoid.py
.\IDAO merge.ipynb
.\IDAO2020.zip
.\magcal_ellipsoid.txt
.\part57.csv
.\part57_fixed.csv
.\part_backup_first.csv
.\part_backup_first_476.csv
.\part_backup_second.csv
.\part_backup_second_second+15.csv
.\plot_ellipsoid.py
.\some-thoughs-about-idao-2020 — копия.ipynb
.\some-thoughs-about-idao-2020-Copy1.ipynb
.\some-thoughs-about-idao-2020-Copy2.ipynb
.\some-thoughs-about-idao-2020-Copy2_0202-Copy1.ipynb
.\some-thoughs-about-idao-2020.ipynb
.\steps1.xlsx
.\steps3.xlsx
.\submission2.csv
.\test.csv
.\train.csv
.\train_cleaned.csv
.\~$steps.xlsx
.\.ipynb_checkpoints\IDAO merge-checkpoint.ipynb
.\.ipynb_checkpoints\some-thoughs-about-idao-2020-checkpoint.ipynb
.\.ipynb_checkpoints\some-thoughs-about-idao-2020-Copy1-checkpoint.ipynb
.\.ipynb_checkpoints\some-thoughs-about-idao-2020-Copy2-checkpoint.ipynb
.\.ipynb_checkpoints\some-thoughs-about-idao-2020-Copy2_0202-Copy1-checkpoint.ipynb
.\IDAO\element.py
.\IDAO

## Basic information

Прогнозирование положения спутников - одна из важнейших задач астрономии. Например, информация о точном положении спутников на орбите необходима, чтобы избежать чрезвычайно опасных столкновений спутников. Каждое столкновение приводит не только к разрушению спутников, но также приводит к тысячам осколков космического мусора. Например, столкновение Иридиум-Коскос в 2009 году увеличило количество космического мусора примерно на 13%. Дальнейшие столкновения могут привести к синдрому Кесслера и недоступности космического пространства. Кроме того, более точный прогноз положения спутника поможет рассчитать более эффективные маневры для экономии топлива и продления срока службы спутника на орбите.

![IMAGE](https://official.contest.yandex.ru/testsys/statement-image?imageId=4628fdaece73e7ead499c8ff0605031a67e880f7fb0df9a285e98956949c0743)

В то же время трудно предсказать точное положение космического объекта, поскольку форма и другие параметры могут быть неизвестны. Кроме того, математические и физические модели не могут полностью учитывать многие факторы, такие как шероховатость поверхности Земли и солнечное давление. Одним из партнеров олимпиады и автором задания является Российский центр астрономических наук (АЦЦ). АСК занимается созданием и эксплуатацией автоматизированных оптоэлектронных систем наблюдения космических объектов и автоматизированных систем обработки информации о космических объектах. Эта проблема имеет к ним особое отношение. Например, ведение Каталога орбит спутников Земли требует многократных наблюдений космических объектов. Чтобы делать такие наблюдения, необходимо знать, куда направить телескопы (видео).

![IMAGE](https://official.contest.yandex.ru/testsys/statement-image?imageId=c98e9ccc7abcbfc9f43daea9f19ceae75dff3c1dca7d677e0690692f574890e2)

Участникам IDAO предлагается уточнить прогноз модели [упрощенного общего возмущения-4 (SGP4)](https://en.wikipedia.org/wiki/Simplified_perturbations_models). SGP4 способен предсказывать множество эффектов, но применяется к околоземным объектам с орбитальным периодом менее 225 минут, в то время как космические объекты на высокой орбите имеют орбитальные периоды до 200 часов. Для определения истинного положения спутников будет получено положение, полученное с использованием более точного симулятора. Впоследствии полученные модели будут применены к реальным классифицированным данным и помогут предсказать положения этих космических объектов.

## Quality metric

Прогнозы координат и скоростей спутников, сделанные участниками, будут сравниваться с истинными, используя метрику [SMAPE](https://en.wikipedia.org/wiki/Symmetric_mean_absolute_percentage_error).

Более конкретно, для спутника и точек времени все представленные прогнозы и истинные значения объединяются в 1-d массивы, затем [SMAPE](https://en.wikipedia.org/wiki/Symmetric_mean_absolute_percentage_error) вычисляется с помощью кода ниже:

In [4]:
def smape(satellite_predicted_values, satellite_true_values): 
    # the division, addition and subtraction are pointwise 
    return np.mean(np.abs((satellite_predicted_values - satellite_true_values) 
        / (np.abs(satellite_predicted_values) + np.abs(satellite_true_values)))) 

После этого SMAPE усредняется по спутникам.

Формула для лидерборда: 

### **SCORE=100∗(1−MEAN(SMAPE))**. 

Этот результат необходимо максимизировать.

## Data description 

Описание данных:

* id — id измерения
* epoch — дата в формате "%Y-%m-%dT%H:%M:%S.%f” (пример 2014-02-01T00:44:57.685)
* sat_id — целочисленный id спутника
* x, y, z, x_sim, y_sim, z_sim — истинные (полученные с помощью мб этого(?) [the precise simulator](https://www.precisesimulation.com/#precise-simulation-software) ) и смоделированные (используя алгоритм SGP4) координаты спутника (км) (km)
* Vx, Vy, Vz, Vx_sim, Vy_sim, Vz_sim — истинные (полученные с помощью мб этого(?) [the precise simulator](https://www.precisesimulation.com/#precise-simulation-software ) ) и смоделированные (используя алгоритм SGP4) скорости спутника (км/c)

Набор данных поезда содержит реальные и смоделированные координаты и скорости для 600 спутников за один месяц. Тестовый набор данных содержит только смоделированные координаты и скорости для 300 спутников из набора данных поезда для следующего месяца. Участники должны предсказать реальные координаты и скорости для этих 300 спутников.

## Output format

Прогнозы в формате .csv. Файл должен содержать семь столбцов: id, x, y, z, Vx, Vy, Vz. Каждая строка в представленном файле соответствовать измерению в тестовом наборе данных. Baseline находится в папке Track 1.

Public score основан на 50% (150 спутников) тестовых данных. Private score основан на оставшихся 50% и будет раскрыт после окончания соревнования.

Только ****последний успешный сабмит**** используется для подсчета public и private результатов нак лидерборде!!!

## Visualization

In [5]:



train = pd.read_csv("{0}/train_cleaned.csv".format(PATH))

test = pd.read_csv("{0}/Track 1/test.csv".format(PATH))
sample_submission = pd.read_csv("{0}/Track 1/submission.csv".format(PATH))

In [6]:
train.shape

(649416, 20)

In [7]:
test.head()

id  sat_id                    epoch         x_sim         y_sim  \
0  3927       1  2014-02-01T00:01:45.162 -13366.891347 -14236.753503   
1  3928       1  2014-02-01T00:22:57.007  -7370.434039 -14498.771520   
2  3929       1  2014-02-01T00:44:08.852   -572.068654 -13065.289498   
3  3930       1  2014-02-01T01:05:20.697   6208.945257  -9076.852425   
4  3931       1  2014-02-01T01:26:32.542  10768.200284  -2199.706707   

         z_sim    Vx_sim    Vy_sim    Vz_sim  
0  6386.774555  4.333815 -0.692764  0.810774  
1  7130.411325  5.077413  0.360609  0.313402  
2  7033.794876  5.519106  2.012830 -0.539412  
3  5548.296900  4.849212  4.338955 -1.869600  
4  2272.014862  1.940505  6.192887 -3.167724

In [8]:

def visualize_data_nth_satelite(df, nsat = 0, in_train = True):
    '''
    This function lets us to visualize the nth's satelite trajectory.
    
    Input params:
    df = dataframe
    nsat = satelite number
    in_train = is a sattelite in train set?
    
    Output params:
    None
    
    '''
    
    if in_train:
        sat_nth_true = df[df.sat_id == nsat][['id', 'x', 'y', 'z', 'epoch' ]]
        sat_nth_true['Label'] = 'Real'
        
        sat_nth_simulated = df[df.sat_id == nsat][['id', 'x_sim', 'y_sim', 'z_sim', 'epoch' ]]
        sat_nth_simulated['Label'] = 'Simulated'
        
        sat_nth_true.columns = ['id', 'x_sim', 'y_sim', 'z_sim','epoch', 'Label' ]
        sat_nth_true = sat_nth_true.append(sat_nth_simulated)
              
        #print(sat_nth_true['Label'] )
            
            
        fig = px.scatter_3d(sat_nth_true, x='x_sim', y='y_sim', z='z_sim',size_max=18,
                    color='id', symbol='Label')
        fig.show()
        
    else:
        sat_nth_model = df[df.sat_id == nsat][['id', 'x_sim', 'y_sim', 'z_sim', 'epoch' ]]
        
        
        
        fig = px.scatter_3d(sat_nth_model, x='x_sim', y='y_sim', z='z_sim',size_max=5,
                    color='id' )
        fig.show()

    return None






In [9]:
visualize_data_nth_satelite(train, nsat = 0, in_train = True)

#diagram 1

In [10]:
visualize_data_nth_satelite(train, nsat = 0, in_train = False)

#diagram 2

In [11]:
visualize_data_nth_satelite(train, nsat = 5, in_train = False)

#diagram 3

## Linear 

In [12]:
def visualize_linear(df , nrow, nsat,  colname_real, colname_val, leg_real_name,leg_sim_name ):
    """
    Just one linear plot.
    
    Input:
    df - Dataframe
    nrow - Number of rows in  visualization
    nsat - satelite number
    colname_real - true series of data
    colname_val - simulated series
    leg_real_name - real colname
    leg_sim_name - simulated colname
    """
    
    df = df[df.sat_id == nsat]
    df = df.head(n=nrow)
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df['epoch'], y=df[colname_real], name=leg_real_name,
                             line_color='deepskyblue'))

    fig.add_trace(go.Scatter(x=df['epoch'], y=df[colname_val], name=leg_sim_name,
                             line_color='dimgray'))

    fig.update_layout(title_text='Time Series with Rangeslider',
                      xaxis_rangeslider_visible=True)
    fig.show()
    
    return None




def visualise_line_3d(df , nrow,  start, nsat , coltrue='seashell' , colsim = 'silver'):
    
    """
    Visualizing 3D lines. Points are coordinats from the dataset and lines are trajectories between them.
    
    Input:
    df - Dataframe
    nrow - Number of rows in  visualization
    start - starting position
    nsat - satelite number
    coltrue - true series of data
    colsim - simulated series
    """
    df = df.loc[df.sat_id == nsat]
    df = df.tail(len(df) - start)
    
    df = df.head(n = nrow)
    
    
    sat_nth_true = df[['id', 'x', 'y', 'z', 'epoch' ]]
    sat_nth_true['Label'] = coltrue
        
    sat_nth_simulated = df[['id', 'x_sim', 'y_sim', 'z_sim', 'epoch' ]]
    sat_nth_simulated['Label'] = 'silver'
        
    sat_nth_true.columns = ['id', 'x_sim', 'y_sim', 'z_sim','epoch', 'Label' ]
    sat_nth_true = sat_nth_true.append(sat_nth_simulated)
    
    
    
    x = sat_nth_true['x_sim']
    y = sat_nth_true['y_sim']
    z = sat_nth_true['z_sim']
    
    color = sat_nth_true['Label']
    
    fig = go.Figure(data=go.Scatter3d(
    x=x, y=y, z=z, 
    marker=dict(
        size=4,
        color=color,
        colorscale='Viridis',
    ),
    line=dict(
        color='darkblue',
        width=0.1
    )
))

    fig.update_layout(
        width=800,
        height=700,
        autosize=False,
        scene=dict(
            camera=dict(
                up=dict(
                    x=0,
                    y=0,
                    z=1
                ),
                eye=dict(
                    x=0,
                    y=1.0707,
                    z=1,
                )
            ),
            aspectratio = dict( x=1, y=1, z=0.7 ),
            aspectmode = 'manual'
        ),
    )

    fig.show()
    return None


In [13]:
train.head()

Unnamed: 0  id                    epoch  sat_id             x  \
0           0   0  2014-01-01 00:00:00.000       0  -8855.823863   
1           1   1  2014-01-01 00:46:43.000       0 -10567.672384   
2           2   2  2014-01-01 01:33:26.001       0 -10578.684043   
3           3   3  2014-01-01 02:20:09.001       0  -9148.251857   
4           4   4  2014-01-01 03:06:52.002       0  -6719.092336   

              y             z        Vx        Vy        Vz         x_sim  \
0  13117.780146 -20728.353233 -0.908303 -3.808436 -2.022083  -8843.131454   
1   1619.746066 -24451.813271 -0.302590 -4.272617 -0.612796 -10555.500066   
2 -10180.467460 -24238.280949  0.277435 -4.047522  0.723155 -10571.858472   
3 -20651.437460 -20720.381279  0.715600 -3.373762  1.722115  -9149.620794   
4 -28929.061629 -14938.907967  0.992507 -2.519732  2.344703  -6729.358857   

          y_sim         z_sim    Vx_sim    Vy_sim    Vz_sim  epoch_year  \
0  13138.221690 -20741.615306 -0.907527 -3.804930 -2.024133        2014   
1   1649.289367 -24473.089556 -0.303704 -4.269816 -0.616468        2014   
2 -10145.939908 -24271.169776  0.274880 -4.046788  0.718768        2014   
3 -20618.200201 -20765.019094  0.712437 -3.375202  1.718306        2014   
4 -28902.271436 -14992.399986  0.989382 -2.522618  2.342237        2014   

   epoch_month  epoch_day  epoch_hour  
0            1          1           0  
1            1          1           0  
2            1          1           1  
3            1          1           2  
4            1          1           3

In [14]:
visualize_linear(train, 22250, 7, 'Vy', 'Vy_sim', "Vy_real", "Vy_sim")


In [15]:
visualize_linear(train, 22250, 3, 'z', 'z_sim', "x_real", "x_sim")

# diagram 4

In [16]:
visualise_line_3d(train , 1000,0, 0, 'seashell' , 'silver' )

#du=iagram 5

## Getting some stats

P.S. Baseline score for the first task may give 66.24 on the leaderboard.

In [17]:
train[['x',	'y',	'z',	'x_sim',	'y_sim', 'z_sim']].describe()

x              y              z          x_sim  \
count  649416.000000  649416.000000  649416.000000  649416.000000   
mean     -817.256382     420.146637     -71.764537    -949.798881   
std     25379.282362   25613.123746   20640.038017   25361.597482   
min   -251938.766780 -291083.016974 -178922.412426 -255037.952966   
25%    -13122.222721  -11618.236264   -7996.881111  -13149.607029   
50%      -507.088544     512.613150      46.115860    -622.785568   
75%     11314.003402   12608.270943    8278.106511   11185.687930   
max    200382.689756  212443.393808  197200.530574  200961.158000   

               y_sim          z_sim  
count  649416.000000  649416.000000  
mean      322.593586     -76.360886  
std     25588.980930   20656.337379  
min   -282851.387908 -180250.922287  
25%    -11730.971158   -7951.797657  
50%       522.659527      57.402722  
75%     12541.952530    8234.125842  
max    209619.553857  198526.091552

In [18]:
train[['Vx',	'Vy',	'Vz',	'Vx_sim',	'Vy_sim',	'Vz_sim']].describe()

Vx             Vy             Vz         Vx_sim  \
count  649416.000000  649416.000000  649416.000000  649416.000000   
mean       -0.000539       0.000466      -0.000110      -0.000512   
std         2.639363       2.597482       2.116584       2.637833   
min        -8.286673      -8.231654      -9.371164      -8.243159   
25%        -1.893148      -1.875470      -1.256456      -1.896717   
50%         0.019957      -0.051690       0.009390       0.021294   
75%         1.960424       1.845428       1.237471       1.955849   
max         8.149559      12.308450       8.644558       7.431851   

              Vy_sim         Vz_sim  
count  649416.000000  649416.000000  
mean        0.000366      -0.000358  
std         2.600686       2.114075  
min        -8.348831      -7.671565  
25%        -1.877706      -1.247318  
50%        -0.012901       0.012020  
75%         1.862671       1.236264  
max         8.021438       8.644165

satelite 11 from a diagram above

In [19]:

train[train.sat_id ==11][['x',	'y',	'z',	'x_sim',	'y_sim', 'z_sim']].describe()

x             y            z         x_sim         y_sim  \
count   2043.000000   2043.000000  2043.000000   2043.000000   2043.000000   
mean   -1176.559323   4980.225806  1689.825253   3557.807252   6679.776171   
std    15272.071840  14303.012709  5076.051521  14789.628957  14120.241956   
min   -25308.106629 -18395.904495 -6690.085606 -18566.606927 -15592.693274   
25%   -16075.313392  -9046.532348 -3301.987088 -10438.290100  -8860.520177   
50%    -1503.028656   6638.043622  2237.173433   4453.019751   8596.327807   
75%    13789.162811  19042.884637  6646.828907  17827.939867  20631.447649   
max    23549.866412  24537.923685  8787.928828  23556.806077  24764.531550   

             z_sim  
count  2043.000000  
mean   2495.410199  
std    5003.591307  
min   -5510.549873  
25%   -2296.476686  
50%    3190.536270  
75%    7225.224497  
max    8873.437790

In [20]:
train[train.sat_id ==11][['Vx',	'Vy',	'Vz',	'Vx_sim',	'Vy_sim',	'Vz_sim']].describe()

Vx           Vy           Vz       Vx_sim       Vy_sim  \
count  2043.000000  2043.000000  2043.000000  2043.000000  2043.000000   
mean     -0.004815     0.008020     0.002470     0.007990    -0.001020   
std       3.031675     2.870655     1.016918     3.029938     2.882216   
min      -4.025402    -4.619670    -1.623454    -3.471612    -4.639587   
25%      -2.904509    -2.784696    -0.987937    -2.709345    -2.550323   
50%      -0.661776    -0.133312    -0.071802    -0.843420     0.240282   
75%       2.849759     2.804146     0.990932     3.005704     2.607269   
max       5.397505     4.813715     1.731678     5.432654     3.743806   

            Vz_sim  
count  2043.000000  
mean     -0.000028  
std       1.021247  
min      -1.629300  
25%      -0.937164  
50%       0.095434  
75%       0.994228  
max       1.380757

Find intersections between train and test frames

In [21]:
print("Equal IDs in train and test: {0} \n Len : {1}".format( set(list(test.sat_id)) & set(list(train.sat_id)) ,  
     len(list(set(list(test.sat_id)) & set(list(train.sat_id))))))


Equal IDs in train and test: {1, 514, 2, 3, 4, 6, 515, 516, 9, 517, 519, 522, 523, 524, 16, 528, 20, 22, 24, 25, 26, 27, 28, 29, 536, 537, 32, 539, 34, 35, 36, 37, 38, 39, 40, 41, 42, 547, 44, 45, 549, 550, 558, 49, 51, 52, 53, 54, 563, 565, 57, 566, 59, 567, 569, 572, 63, 64, 575, 578, 579, 68, 580, 70, 583, 584, 75, 587, 588, 593, 82, 595, 84, 596, 86, 597, 89, 90, 91, 92, 93, 96, 98, 100, 101, 102, 105, 106, 109, 110, 112, 113, 114, 117, 118, 120, 121, 123, 124, 125, 126, 127, 128, 130, 132, 133, 135, 138, 142, 143, 144, 145, 149, 151, 152, 153, 155, 156, 158, 159, 160, 162, 164, 165, 166, 542, 169, 170, 172, 173, 543, 177, 178, 544, 183, 186, 187, 188, 191, 193, 194, 195, 197, 548, 203, 205, 206, 207, 208, 209, 210, 211, 213, 219, 220, 222, 223, 225, 227, 228, 229, 230, 233, 236, 239, 240, 241, 242, 243, 244, 245, 247, 248, 251, 252, 253, 254, 261, 263, 264, 265, 268, 270, 275, 277, 278, 281, 284, 288, 292, 293, 294, 298, 299, 301, 304, 306, 309, 310, 312, 314, 316, 319, 324, 326, 

Compare them:

In [22]:
train[train.sat_id==373].head(n=3)

Unnamed: 0      id                    epoch  sat_id             x  \
398558      398558  398558  2014-01-01 00:00:00.000     373  10644.366120   
398559      398559  398559  2014-01-01 00:33:04.283     373    170.211241   
398560      398560  398560  2014-01-01 01:06:08.567     373 -10752.511579   

                   y           z        Vx        Vy        Vz         x_sim  \
398558   9352.428980 -135.801648 -4.288014  4.881531  0.080865  10742.901056   
398559  15933.885456   45.586884 -5.760014  1.674447  0.093873    300.216514   
398560  16637.264588  216.125678 -5.066883 -0.722181  0.075941 -10638.132950   

               y_sim       z_sim    Vx_sim    Vy_sim    Vz_sim  epoch_year  \
398558   9261.510705 -136.485772 -4.258222  4.901513  0.083878        2014   
398559  15901.132592   50.512896 -5.759529  1.705000  0.096356        2014   
398560  16650.412376  224.867549 -5.079530 -0.706927  0.077304        2014   

        epoch_month  epoch_day  epoch_hour  
398558            1          1           0  
398559            1          1           0  
398560            1          1           1

In [23]:
train[train.sat_id==373].tail(n=3)

Unnamed: 0      id                    epoch  sat_id             x  \
399905      399905  399905  2014-01-31 22:27:09.718     373 -26861.854782   
399906      399906  399906  2014-01-31 23:00:14.002     373 -31489.079285   
399907      399907  399907  2014-01-31 23:33:18.285     373 -34544.216621   

                  y           z        Vx        Vy        Vz         x_sim  \
399905  8029.004839  420.622539 -2.782811 -2.577567  0.035152 -20244.020924   
399906  2713.436965  476.535384 -1.910283 -2.743726  0.021730 -26777.778704   
399907 -2752.917364  508.634782 -1.191069 -2.746014  0.011001 -31395.066872   

               y_sim      z_sim    Vx_sim    Vy_sim    Vz_sim  epoch_year  \
399905  12932.271639  391.89155 -3.839074 -2.098451  0.054841        2014   
399906   8209.240539  480.29461 -2.778447 -2.588776  0.035109        2014   
399907   2864.672013  534.17983 -1.903835 -2.760884  0.019831        2014   

        epoch_month  epoch_day  epoch_hour  
399905            1         31          22  
399906            1         31          23  
399907            1         31          23

In [24]:
test[test.sat_id==373].head(n=3)

id  sat_id                    epoch         x_sim         y_sim  \
168287  759728     373  2014-02-01T00:06:22.568 -34433.378274  -2639.622605   
168288  759729     373  2014-02-01T00:39:26.852 -36154.422520  -8051.318187   
168289  759730     373  2014-02-01T01:12:31.135 -36755.116028 -13218.490103   

             z_sim    Vx_sim    Vy_sim    Vz_sim  
168287  561.133835 -1.180291 -2.766173  0.007780  
168288  566.586819 -0.570773 -2.675457 -0.001965  
168289  554.462167 -0.047234 -2.523710 -0.010020

In [25]:
test[test.sat_id==373].tail(n=3)

id  sat_id                    epoch         x_sim         y_sim  \
169503  760944     373  2014-02-28T22:21:11.162  16284.383273 -11392.093149   
169504  760945     373  2014-02-28T22:54:15.446  15979.123822   -476.271884   
169505  760946     373  2014-02-28T23:27:19.729   9817.653060  10230.033398   

             z_sim    Vx_sim    Vy_sim    Vz_sim  
169503 -334.806860  0.898084  5.026361  0.009328  
169504 -275.920577 -1.453411  5.805872  0.053427  
169505 -117.801985 -4.704849  4.476517  0.102571

It seems test data is February observations of some train January satellites. 300 satelite private observations for the first task, other 300 for the second one 

Вывод: всего 600 временных рядов, описывающих позицию и скорость перемещения в трёхмерном пространстве за январь. Спутники вращаются вокруг Земли. Наблюдения идут с интервалом полчаса. Также они зациклены, т.е. несколько раз обходят орбиту.
    
Тестовые данные - данные февраля. 300 спутников на первое задание, триста на задание с кодом. Данные не особо отличаются статистически (в общем), поскольку отклонения в разные стороны компенсируют друг друга, но по отдельным спутникам как визуально, так и статистичеки имеются отклонения(по положению в пространстве), например №11 между истинным значением и алгоритмом, скорость перемещения же примерно одинаковая. Имеется предположение, что скорость может изменяться относительно позиции над Землёй (это нужно бы уточнить у знающих людей, сайтов). 

Скорее всего по данным координатам можно вычислить географическую позицию спутника. Вопрос в том, нужно ли это делать. 

## Базовый алгоритм как и котлетки будет ближе к выходным

![FILE](https://sun9-6.userapi.com/c836633/v836633645/1994f/VjLC0yXrsNA.jpg)

## Attemption to improve a naive baseline solution

This approach is based on the third diagram and the fifth one. It's obviously the data is looped and has an periodicity. Every single point has a bias depends on points before. We will consider corresponding points as values of some function (maybe linear or not). When we aproximane them by the function and extrapolate the function we will be able to recieve some "truly labels" of February observations. 

Let's check this idea. Firstly we should find length of periodicity.

In [26]:
visualise_line_3d(train , 24,0, 0, 'seashell' , 'silver' )

C**ount them manually. It's 24 . Check it

In [27]:
visualise_line_3d(train , 23,0, 120, 'seashell' , 'silver' )

Another one

In [28]:
#train[train.sat_id == 342]

In [29]:
visualise_line_3d(train , 24,0, 494, 'seashell' , 'silver' )

Gotta validate it

In [30]:
def find_interval(df, nsat):
    '''
    Function is based on Euclidean metric between points.
    
    eudclidean(a[0], min(a[1], .... , a[n])) --> index of second element is period
    
    Input:
    nsat - satelite number
    
    '''
    x = df.loc[df.sat_id == nsat]['x'].tolist()
    y = df.loc[df.sat_id == nsat]['y'].tolist()
    z = df.loc[df.sat_id == nsat]['z'].tolist()
    
    distances = []
    
    for i in range(1, len(x)):
        distances.append(distance.euclidean((x[0], y[0], z[0]), (x[i], y[i], z[i])))
    index  = distances.index(min(distances)) +1
    
    return index, len(x)
    

In [31]:
for i in range(599):
    if find_interval(train, i):
        print(i, find_interval(train, i))

0 (24, 956)
1 (24, 2106)
2 (48, 416)
3 (120, 353)
4 (24, 1207)
5 (1679, 3531)
6 (95, 418)
7 (24, 233)
8 (24, 2578)
9 (24, 330)
10 (24, 1764)
11 (24, 2043)
12 (24, 296)
13 (24, 1055)
14 (24, 809)
15 (24, 2919)
16 (48, 195)
17 (24, 725)
18 (24, 1524)
19 (24, 484)
20 (171, 195)
21 (575, 689)
22 (122, 266)
23 (24, 249)
24 (24, 499)
25 (24, 750)
26 (47, 128)
27 (24, 1076)
28 (404, 455)
29 (24, 466)
30 (24, 1171)
31 (119, 319)
32 (24, 304)
33 (24, 1178)
34 (24, 1077)
35 (25, 311)
36 (24, 2633)
37 (24, 2178)
38 (24, 799)
39 (48, 546)
40 (24, 1146)
41 (24, 1956)
42 (24, 817)
43 (24, 454)
44 (24, 3526)
45 (24, 342)
46 (24, 270)
47 (24, 1206)
48 (24, 1001)
49 (24, 1407)
50 (1055, 1194)
51 (24, 1425)
52 (215, 425)
53 (24, 2454)
54 (24, 2451)
55 (24, 778)
56 (143, 316)
57 (24, 1241)
58 (24, 495)
59 (24, 2580)
60 (24, 4287)
61 (24, 221)
62 (24, 445)
63 (24, 1440)
64 (24, 231)
65 (24, 609)
66 (24, 194)
67 (24, 786)
68 (24, 2869)
69 (24, 418)
70 (24, 198)
71 (337, 1410)
72 (24, 596)
73 (24, 679)
74 (

In [32]:
visualise_line_3d(train , 24,0, 1, 'seashell' , 'silver' )

Anyway period is 24 points

In [33]:
train[train.sat_id == 1]

Unnamed: 0    id                    epoch  sat_id             x  \
956          956   956  2014-01-01 00:00:00.000       1  10390.313089   
957          957   957  2014-01-01 00:21:11.845       1  11195.606833   
958          958   958  2014-01-01 00:42:23.690       1   8235.556436   
959          959   959  2014-01-01 01:03:35.534       1   3560.149776   
960          960   960  2014-01-01 01:24:47.379       1  -1580.476891   
...          ...   ...                      ...     ...           ...   
3057        3057  3057  2014-01-31 22:15:45.938       1 -33092.618399   
3058        3058  3058  2014-01-31 22:36:57.783       1 -32678.193673   
3059        3059  3059  2014-01-31 22:58:09.628       1 -31665.342406   
3060        3060  3060  2014-01-31 23:19:21.473       1 -30034.378237   
3061        3061  3061  2014-01-31 23:40:33.318       1 -27756.260690   

                 y            z        Vx        Vy        Vz         x_sim  \
956   -2796.458271  3179.562085  2.520477  6.149930 -2.827599  10405.813755   
957    5078.653968  -839.076593 -1.126667  5.826412 -3.255872  11199.853336   
958   11445.904263 -4680.514023 -3.230227  4.126433 -2.704441   8239.504004   
959   15634.195146 -7654.177182 -3.964696  2.520867 -1.978151   3569.107805   
960   18023.318335 -9755.287599 -4.050865  1.296388 -1.346512  -1566.253652   
...            ...          ...       ...       ...       ...           ...   
3057   -281.511542 -1582.378975  0.094088 -1.839427  1.337545 -29406.078919   
3058  -2611.293944   127.879530  0.559090 -1.818598  1.347891 -27882.742274   
3059  -4892.533056  1835.695504  1.036204 -1.762460  1.333303 -25577.429154   
3060  -7077.220106  3507.336506  1.532305 -1.665557  1.290191 -22432.558095   
3061  -9107.885238  5102.708242  2.055278 -1.518181  1.211938 -18382.812351   

             y_sim        z_sim    Vx_sim    Vy_sim    Vz_sim  epoch_year  \
956   -2771.180760  3166.926302  2.508879  6.152996 -2.826227        2014   
957    5102.405255  -845.930363 -1.130992  5.822303 -3.250049        2014   
958   11465.137350 -4680.291877 -3.227356  4.123931 -2.700255        2014   
959   15652.050271 -7650.341207 -3.960215  2.520907 -1.976723        2014   
960   18042.143340 -9750.982621 -4.047005  1.297625 -1.347010        2014   
...            ...          ...       ...       ...       ...         ...   
3057  -2719.769909 -1476.299104  0.903445 -2.329687  1.355335        2014   
3058  -5634.903507   259.572177  1.498239 -2.242285  1.367602        2014   
3059  -8389.868466  1986.924648  2.134397 -2.074305  1.340251        2014   
3060 -10865.836350  3646.968029  2.819524 -1.797623  1.258773        2014   
3061 -12896.945935  5156.151522  3.557107 -1.364583  1.097643        2014   

      epoch_month  epoch_day  epoch_hour  
956             1          1           0  
957             1          1           0  
958             1          1           0  
959             1          1           1  
960             1          1           1  
...           ...        ...         ...  
3057            1         31          22  
3058            1         31          22  
3059            1         31          22  
3060            1         31          23  
3061            1         31          23  

[2106 rows x 20 columns]

In [34]:
train[train.sat_id == 2]

Unnamed: 0    id                    epoch  sat_id             x  \
3062        3062  3062  2014-01-01 00:00:00.000       2  33148.668886   
3063        3063  3063  2014-01-01 01:47:19.603       2  34524.849803   
3064        3064  3064  2014-01-01 03:34:39.205       2  26209.000418   
3065        3065  3065  2014-01-01 05:21:58.808       2  12865.236538   
3066        3066  3066  2014-01-01 07:09:18.410       2  -2122.829466   
...          ...   ...                      ...     ...           ...   
3473        3473  3473  2014-01-31 15:11:16.665       2  12081.577200   
3474        3474  3474  2014-01-31 16:58:36.268       2  -3010.161911   
3475        3475  3475  2014-01-31 18:45:55.871       2 -17936.515013   
3476        3476  3476  2014-01-31 20:33:15.473       2 -31877.895629   
3477        3477  3477  2014-01-31 22:20:35.076       2 -44436.463847   

                 y             z        Vx        Vy        Vz         x_sim  \
3062 -14110.640743   -968.074861  1.128804  2.826089 -2.540709  33421.694365   
3063   5438.883966 -16279.040266 -0.652929  3.071909 -2.099883  34479.954736   
3064  23782.292036 -27262.969421 -1.795643  2.552720 -1.303775  26013.271173   
3065  37948.818156 -33308.619162 -2.262068  1.847384 -0.604569  12658.477848   
3066  47734.661499 -35452.597642 -2.350057  1.209939 -0.090077  -2284.126205   
...            ...           ...       ...       ...       ...           ...   
3473  38081.152569 -33410.922656 -2.284614  1.830249 -0.576634  -2460.789528   
3474  47749.684829 -35371.137421 -2.360235  1.191185 -0.061563 -17344.876465   
3475  53668.698857 -34528.070970 -2.255529  0.665329  0.302313 -31278.866123   
3476  56530.667561 -31704.732701 -2.064600  0.238173  0.559875 -43856.918294   
3477  56902.596290 -27476.869612 -1.830810 -0.111301  0.742738 -54869.649941   

             y_sim         z_sim    Vx_sim    Vy_sim    Vz_sim  epoch_year  \
3062 -13513.388445  -1551.416776  1.075190  2.851149 -2.530708        2014   
3063   6084.116849 -16720.234615 -0.691089  3.063011 -2.069545        2014   
3064  24325.975371 -27516.436985 -1.805296  2.533284 -1.277723        2014   
3065  38377.608320 -33429.920347 -2.257234  1.831557 -0.588909        2014   
3066  48080.268831 -35501.065963 -2.340856  1.199491 -0.082207        2014   
...            ...           ...       ...       ...       ...         ...   
3473  47783.331431 -35423.410082 -2.350571  1.206935 -0.073701        2014   
3474  53801.612796 -34657.294233 -2.251916  0.680931  0.290594        2014   
3475  56758.540793 -31905.643451 -2.065689  0.252613  0.549261        2014   
3476  57216.274744 -27741.079582 -1.835502 -0.098539  0.733529        2014   
3477  55614.386183 -22572.665681 -1.581721 -0.389541  0.863631        2014   

      epoch_month  epoch_day  epoch_hour  
3062            1          1           0  
3063            1          1           1  
3064            1          1           3  
3065            1          1           5  
3066            1          1           7  
...           ...        ...         ...  
3473            1         31          15  
3474            1         31          16  
3475            1         31          18  
3476            1         31          20  
3477            1         31          22  

[416 rows x 20 columns]

In [35]:
def visualize_trajectories(df, nsat):
    
    
    """
    Input:
    df - dataframe
    
    nsat - satelite number
    """
    df = df.loc[df.sat_id == nsat]
    
    
    df['period'] = df['id']%24

    fig = px.line_3d(df, x="x", y="y", z="z", color='period')
    fig.show()
    
    
    
    


In [36]:
visualize_trajectories(train, 5)

INFO:numexpr.utils:Note: NumExpr detected 12 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [37]:
visualize_trajectories(train, 27)

## Prophet

In [38]:
train.head()

Unnamed: 0  id                    epoch  sat_id             x  \
0           0   0  2014-01-01 00:00:00.000       0  -8855.823863   
1           1   1  2014-01-01 00:46:43.000       0 -10567.672384   
2           2   2  2014-01-01 01:33:26.001       0 -10578.684043   
3           3   3  2014-01-01 02:20:09.001       0  -9148.251857   
4           4   4  2014-01-01 03:06:52.002       0  -6719.092336   

              y             z        Vx        Vy        Vz         x_sim  \
0  13117.780146 -20728.353233 -0.908303 -3.808436 -2.022083  -8843.131454   
1   1619.746066 -24451.813271 -0.302590 -4.272617 -0.612796 -10555.500066   
2 -10180.467460 -24238.280949  0.277435 -4.047522  0.723155 -10571.858472   
3 -20651.437460 -20720.381279  0.715600 -3.373762  1.722115  -9149.620794   
4 -28929.061629 -14938.907967  0.992507 -2.519732  2.344703  -6729.358857   

          y_sim         z_sim    Vx_sim    Vy_sim    Vz_sim  epoch_year  \
0  13138.221690 -20741.615306 -0.907527 -3.804930 -2.024133        2014   
1   1649.289367 -24473.089556 -0.303704 -4.269816 -0.616468        2014   
2 -10145.939908 -24271.169776  0.274880 -4.046788  0.718768        2014   
3 -20618.200201 -20765.019094  0.712437 -3.375202  1.718306        2014   
4 -28902.271436 -14992.399986  0.989382 -2.522618  2.342237        2014   

   epoch_month  epoch_day  epoch_hour  
0            1          1           0  
1            1          1           0  
2            1          1           1  
3            1          1           2  
4            1          1           3

In [39]:
def predict_nth_satelite(train, test, ids):
    
    fit = ["x_sim", "y_sim", "z_sim", "Vx_sim", "Vy_sim", "Vz_sim"]


    predicted = ["x", "y", "z", "Vx", "Vy", "Vz"]
    for i in range(6):
        for_prophet = train[train.sat_id == ids][['epoch', fit[i]]]
        for_prophet.columns = ['ds', 'y']       
        for_prophet_test = test[test.sat_id == ids]['epoch']
        for_prophet_test.name = 'ds'
        for_prophet_test = for_prophet_test.to_frame()

        for_prophet_test.columns = ['ds']

        m = Prophet()

        m.fit(for_prophet)
        future = m.predict(for_prophet_test)
        test.loc[test.sat_id == ids, predicted[i]] = future['trend']

        
    return train, test 

In [40]:
test.head()

id  sat_id                    epoch         x_sim         y_sim  \
0  3927       1  2014-02-01T00:01:45.162 -13366.891347 -14236.753503   
1  3928       1  2014-02-01T00:22:57.007  -7370.434039 -14498.771520   
2  3929       1  2014-02-01T00:44:08.852   -572.068654 -13065.289498   
3  3930       1  2014-02-01T01:05:20.697   6208.945257  -9076.852425   
4  3931       1  2014-02-01T01:26:32.542  10768.200284  -2199.706707   

         z_sim    Vx_sim    Vy_sim    Vz_sim  
0  6386.774555  4.333815 -0.692764  0.810774  
1  7130.411325  5.077413  0.360609  0.313402  
2  7033.794876  5.519106  2.012830 -0.539412  
3  5548.296900  4.849212  4.338955 -1.869600  
4  2272.014862  1.940505  6.192887 -3.167724

In [41]:
test["x"], test["y"], test["z"], test["Vx"], test["Vy"], test["Vz"] = None, None, None, None, None, None

In [42]:
ids = list(set(list(test.sat_id)) & set(list(train.sat_id)))



cnt = 0

# for i in ids:
#     print("Done {0}".format(i, cnt/len(ids)))
#     train, test = predict_nth_satelite(train,test, i)
#     cnt+=1


## Center

In [43]:
def ellipsoid_fit(X):
    x = X[:, 0]
    y = X[:, 1]
    z = X[:, 2]
    D = np.array([x * x + y * y - 2 * z * z,
                 x * x + z * z - 2 * y * y,
                 2 * x * y,
                 2 * x * z,
                 2 * y * z,
                 2 * x,
                 2 * y,
                 2 * z,
                 1 - 0 * x])
    d2 = np.array(x * x + y * y + z * z).T # rhs for LLSQ
    u = np.linalg.solve(D.dot(D.T), D.dot(d2))
    a = np.array([u[0] + 1 * u[1] - 1])
    b = np.array([u[0] - 2 * u[1] - 1])
    c = np.array([u[1] - 2 * u[0] - 1])
    v = np.concatenate([a, b, c, u[2:]], axis=0).flatten()
    A = np.array([[v[0], v[3], v[4], v[6]],
                  [v[3], v[1], v[5], v[7]],
                  [v[4], v[5], v[2], v[8]],
                  [v[6], v[7], v[8], v[9]]])

    center = np.linalg.solve(- A[:3, :3], v[6:9])

    translation_matrix = np.eye(4)
    translation_matrix[3, :3] = center.T

    R = translation_matrix.dot(A).dot(translation_matrix.T)

    evals, evecs = np.linalg.eig(R[:3, :3] / -R[3, 3])
    evecs = evecs.T

    radii = np.sqrt(1. / np.abs(evals))
    radii *= np.sign(evals)

    return center, evecs, radii



In [44]:
# from ellipsoid_fit import *
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

def show_ellipse_stat(train, start, ids):
    """
    Getting elipse center and some more features
    """
    
    #data = np.array(train[train.sat_id == ids][['x', 'y', 'z']].head(24))
    sim = train.loc[train.sat_id == ids][[ 'x_sim', 'y_sim', 'z_sim']]
    train = train.loc[train.sat_id == ids][[ 'x', 'y', 'z']]
    center_real = []
    center_sim = []
    for i in range(0, len(train)//24):
        
        print(i)
        
        start = i *24
        
        
        
        real = np.array(train.tail(len(train) - start).head(23))
        simulated = np.array(sim.tail(len(train) - start).head(23))

        frames = [['real', real, center_real], [ 'simulated', simulated, center_sim] ]

        for j in frames:
            center, evecs, radii = ellipsoid_fit(j[1])


            a, b, c = radii



            r = pow(a * b * c, 1. / 3.) #()** (1. / 3.)

            D = np.array([[r/a, 0., 0.], [0., r/b, 0.], [0., 0., r/c]])



            transformation = np.dot(evecs, D)

            np.dot(transformation, evecs.T)

            print('_______________________')

            print('center: ', center)
            print('radii: ', radii)
            print('evecs: ', evecs)

    
            print('transformation:')
            #print(transformation)
            j[2].append(center.tolist())

            
    print("____________________________________________________________________")
    return frames[0][2], frames[1][2]



In [45]:
train.loc[train.sat_id == 1].head()

Unnamed: 0   id                    epoch  sat_id             x  \
956         956  956  2014-01-01 00:00:00.000       1  10390.313089   
957         957  957  2014-01-01 00:21:11.845       1  11195.606833   
958         958  958  2014-01-01 00:42:23.690       1   8235.556436   
959         959  959  2014-01-01 01:03:35.534       1   3560.149776   
960         960  960  2014-01-01 01:24:47.379       1  -1580.476891   

                y            z        Vx        Vy        Vz         x_sim  \
956  -2796.458271  3179.562085  2.520477  6.149930 -2.827599  10405.813755   
957   5078.653968  -839.076593 -1.126667  5.826412 -3.255872  11199.853336   
958  11445.904263 -4680.514023 -3.230227  4.126433 -2.704441   8239.504004   
959  15634.195146 -7654.177182 -3.964696  2.520867 -1.978151   3569.107805   
960  18023.318335 -9755.287599 -4.050865  1.296388 -1.346512  -1566.253652   

            y_sim        z_sim    Vx_sim    Vy_sim    Vz_sim  epoch_year  \
956  -2771.180760  3166.926302  2.508879  6.152996 -2.826227        2014   
957   5102.405255  -845.930363 -1.130992  5.822303 -3.250049        2014   
958  11465.137350 -4680.291877 -3.227356  4.123931 -2.700255        2014   
959  15652.050271 -7650.341207 -3.960215  2.520907 -1.976723        2014   
960  18042.143340 -9750.982621 -4.047005  1.297625 -1.347010        2014   

     epoch_month  epoch_day  epoch_hour  
956            1          1           0  
957            1          1           0  
958            1          1           0  
959            1          1           1  
960            1          1           1

In [46]:
center_real, center_sim = show_ellipse_stat(train,0, 5)

0
_______________________
center:  [-912.07901212   -5.91908039  -96.2566907 ]
radii:  [   96.45387459 14957.22185057 14929.5040903 ]
evecs:  [[ 1.03897503e-01  2.27266483e-02 -9.94328320e-01]
 [-9.94584801e-01 -1.65525306e-04 -1.03928086e-01]
 [ 2.52652365e-03 -9.99741703e-01 -2.25863813e-02]]
transformation:
_______________________
center:  [-891.09805264   -0.95927581  -94.6221561 ]
radii:  [  -35.18867089 14931.62013797 14897.78065913]
evecs:  [[ 0.10388325  0.02264862 -0.99433159]
 [-0.99395472 -0.03334859 -0.10460349]
 [ 0.03552868 -0.99918713 -0.01904734]]
transformation:
1
_______________________
center:  [-904.03662903   -2.34626199  -97.36941258]
radii:  [ -118.84238842 14948.50014423 14920.51033334]
evecs:  [[ 1.03898519e-01  2.29612859e-02 -9.94322823e-01]
 [-9.94586105e-01  4.97424217e-04 -1.03914543e-01]
 [ 1.89141130e-03 -9.99736231e-01 -2.28886576e-02]]
transformation:
_______________________
center:  [-882.16576313    2.55995691  -93.46737406]
radii:  [  -28.6851473  1

In [47]:
print(len(center_real), len( center_sim))

147 147


In [48]:
for i in range(len(center_real)):
    print("_________________________________")
    print(center_real[i],center_sim[i] )

_________________________________
[-912.0790121152843, -5.919080391037917, -96.25669070443222] [-891.0980526373829, -0.9592758144904306, -94.62215610141128]
_________________________________
[-904.0366290307527, -2.346261991053417, -97.36941257679047] [-882.1657631280723, 2.5599569086910483, -93.46737406468297]
_________________________________
[-1657.418028862813, -127.74884809032439, -177.72523895076895] [-917.1794613992868, -3.003323467595312, -96.02077334688157]
_________________________________
[-902.9694494194107, 1.2543211533755727, -96.59993762533836] [-918.029185503143, -1.4107791589667034, -96.36234161476462]
_________________________________
[-922.1661125566314, -0.4773253532473868, -97.77718016350047] [-912.2372442669006, 1.993396731642531, -97.53485551025993]
_________________________________
[-892.338834569572, 6.6474799194066945, -95.13470390313734] [-906.3578961811086, 4.6621230622759136, -95.92218485921279]
_________________________________
[-937.7684490406536, 0.05935

In [49]:
from statsmodels.tsa.stattools import adfuller
def test_stationarity(timeseries):
    
    #Determing rolling statistics
    rolmean = timeseries.rolling(24).mean()
    #ts_log.rolling(12).mean()
    
    rolstd = timeseries.rolling(24).std()

    #Plot rolling statistics:
    orig = plt.plot(timeseries, color='blue',label='Original')
    mean = plt.plot(rolmean, color='red', label='Rolling Mean')
    std = plt.plot(rolstd, color='black', label = 'Rolling Std')
    plt.legend(loc='best')
    plt.title('Rolling Mean & Standard Deviation')
    plt.show(block=False)
    
    #Perform Dickey-Fuller test:
    print('Results of Dickey-Fuller Test:')
    dftest = adfuller(timeseries, autolag='AIC')
    dfoutput = pd.Series(dftest[0:4], index=['Test Statistic','p-value','#Lags Used','Number of Observations Used'])
    for key,value in dftest[4].items():
        dfoutput['Critical Value (%s)'%key] = value
    print(dfoutput)

In [50]:
def interpolation_and_extrapolation_fitting(train, test, sat_id, colu, t_size):
    
    train_size = int(len(train[train.sat_id == sat_id]) - len(train[train.sat_id == sat_id])* t_size)
    test_size = int(len(train[train.sat_id == sat_id])) - train_size
    print(train_size, test_size)
    y = train[train.sat_id == sat_id][ colu][:train_size]
    y_sim = train[train.sat_id == sat_id][ "{0}_sim".format(colu)][:train_size]
    
    
    y_sim.index = train[train.sat_id == sat_id]['id'][:train_size]
    
    
    y.index = train[train.sat_id == sat_id]['id'][:train_size]
    
    y_test = train[train.sat_id == sat_id][ colu][train_size:]
    
    y_test.index = train[train.sat_id == sat_id]['id'][train_size:]
    
    
    y_test_sim = train[train.sat_id == sat_id][  "{0}_sim".format(colu)][train_size:]
    
    y_test_sim.index = train[train.sat_id == sat_id]['id'][train_size:]
    
    
    
    p = d = q = range(0, 2)

    # Generate all different combinations of p, q and q triplets
    
    pdq = list(itertools.product(p, d, q))
    
    seasonal_pdq = [(x[0], x[1], x[2], 24) for x in list(itertools.product(p, d, q))]

 
    
    AIC = 999999
    best_param = ()
    best_seas = ()
    
    SMOPE = 0
    best_param_smope = ()
    best_seas_smope = ()
    
    for param in pdq:
        for param_seasonal in seasonal_pdq:
            try:
                mod = sm.tsa.statespace.SARIMAX(y,
                                                order=param,
                                                seasonal_order=param_seasonal,
                                                enforce_stationarity=False,
                                                enforce_invertibility=False,
                                              # exog = y_sim
                                               )

                results = mod.fit()
                
                pred_uc = results.predict(start = len(y), end=len(y)+len(y_test)-1).tolist()
                
                metric_new = 100*(1- smape(pred_uc, y_test))
                
                metric_sim = 100*(1- smape(y_test_sim, y_test)) 
                
                print('ARIMA{}x{}12 - AIC:{} SMOPE NEW:{}  SMOPE SIMULATED: {}'.format(
                    param, param_seasonal, results.aic, metric_new, metric_sim 
                                                                   ))
                if SMOPE > metric_new:
                        best_param = param
                        best_seas = param_seasonal
                        SMOPE = metric_new
                        
                if AIC > results.aic:
                        best_param = param
                        best_seas = param_seasonal
                        AIC = metric_new
                    
                    
            except Exception as e:
                print(e)
                continue
    print("Best AIC: {0} \n Best param: {1} \n  Best param_seasonal: {2} \n ".format(param, param_seasonal, results.aic))
                
    mod = sm.tsa.statespace.SARIMAX(y,
                                order=param,
                                seasonal_order=param_seasonal,
                                enforce_stationarity=False,
                                enforce_invertibility=False)

    results = mod.fit()
    #results.save('./models/model_save_sarimax_{}_{}.p'.format(sat_id, colu ))
    
#     pred_uc = results.get_forecast(steps=len(y_test) )
#     pred_ci = pred_uc.conf_int()

    #test.loc[test.sat_id == sat_id, colu] = results.predict(start = len(y), end=len(y)+len(y_test)-1
    #
 #   ).tolist()
    return test
#smape(satellite_predicted_values, satellite_true_values)

In [51]:
def interpolation_and_extrapolation(train, test, test_sec, sat_id, sizes, test_and_train,  colu, speed_colu, speed_colu_sim):
    if sat_id in test_and_train:
        y = train[train.sat_id == sat_id][ colu].tolist()#[:240]
        y_sim = train[train.sat_id == sat_id][ "{0}_sim".format(colu)].tolist()
        #y.index = train[train.sat_id == sat_id]['id']#[:240]
        if sat_id in test_and_train:
            y_test = test[test.sat_id == sat_id][ colu].tolist()
        else:
            y_test = test_sec[test_sec.sat_id == sat_id][ colu].tolist()

        #y_test.index = test[test.sat_id == sat_id][ 'id']

        p = d = q = range(0, 2)

        # Generate all different combinations of p, q and q triplets

        pdq = list(itertools.product(p, d, q))

        seasonal_pdq = [(x[0], x[1], x[2], 24) for x in list(itertools.product(p, d, q))]



        AIC = 999999
        best_param = ()
        best_seas = ()

        for param in pdq:
            for param_seasonal in seasonal_pdq:
                try:
                    mod = sm.tsa.statespace.SARIMAX(y,
                                                    order=param,
                                                    seasonal_order=param_seasonal,
                                                    enforce_stationarity=False,
                                                    enforce_invertibility=False,
                                                   #exog = y_sim
                                                   )

                    results = mod.fit()



                    if AIC > results.aic:
                        #print(AIC, results.aic)
                        best_param = param
                        best_seas = param_seasonal
                        AIC = results.aic
                    print('ARIMA{}x{}12 - AIC:{}'.format(param, param_seasonal, results.aic 
                                                                       ))   
                    #print('BEST{}x{}12 - AIC:{}'.format( best_param, best_seas, AIC
                        #                                               ))    




                except Exception as e:
                    print(e)
                    continue
        print("Best AIC: {0} \n Best param: {1} \n  Best param_seasonal: {2} \n ".format(best_param, best_seas, AIC))




        try: 

            mod = sm.tsa.statespace.SARIMAX(y,
                                    order=best_param,
                                    seasonal_order=best_seas,
                                    enforce_stationarity=False,
                                    enforce_invertibility=False)

            results = mod.fit()

        #results.save('./models/model_save_sarimax_{}_{}.p'.format(sat_id, colu ))


            #print('ARIMA - AIC:{}'.format(results.aic  ))
            if sat_id in test_and_train:
                test.loc[test.sat_id == sat_id, colu] = results.predict(start = len(y), end=len(y)+len(y_test)-1).tolist()
            else:
                print(len(y), len(y)+len(y_test)-1)
                test_sec.loc[test_sec.sat_id == sat_id, colu] = results.predict(start = len(y), end=len(y)+len(y_test)-1).tolist()
        except Exception as e:
            print(e)
            if sat_id in test_and_train:
                test.loc[test.sat_id == sat_id, colu] = test.loc[test.sat_id == sat_id, "{0}_sim".format(colu)]
            else:
                #print(len(y), len(y)+len(y_test)-1)
                test_sec.loc[test_sec.sat_id == sat_id, colu] = test_sec.loc[test_sec.sat_id == sat_id, "{0}_sim".format(colu)]
        if colu == 'Vz':
            test.to_csv("part_backup_first.csv", index=False)
            test_sec.to_csv("part_backup_second.csv", index=False)
    return test, test_sec




In [52]:
def find_lin_coef(df, coord):
    train_len = int(df.shape[0] * 0.8)
    x = df[coord]
    x = x[:, np.newaxis]
    y = np.arange(0,len(df))
    y = y[:, np.newaxis]
    train_x = y[:train_len]
    train_y = x[:train_len]
    # test_x = y[train_len:]
    # test_y = x[train_len:]
    linear_model = LinearRegression()
    linear_model.fit(train_x, train_y)
    # lin_res = linear_model.predict(test_x)
    return [linear_model.coef_[0][0], linear_model.intercept_[0]]



def interpolation_and_extrapolation_test(train, test, test_sec, sat_id, sizes, test_and_train,  colu, speed_colu, speed_colu_sim, tune):
    if sat_id not in test_and_train:
        print("count")
        y = train[train.sat_id == sat_id][ colu].tolist()#[:240]
        y_sim = train[train.sat_id == sat_id][ "{0}_sim".format(colu)].tolist()
        #y.index = train[train.sat_id == sat_id]['id']#[:240]
        if sat_id in test_and_train:
            y_test = test[test.sat_id == sat_id][ colu].tolist()
        else:
            y_test = test_sec[test_sec.sat_id == sat_id][ colu].tolist()

        #y_test.index = test[test.sat_id == sat_id][ 'id']

        p = d = q = range(0, 2)

        # Generate all different combinations of p, q and q triplets

        pdq = list(itertools.product(p, d, q))

        seasonal_pdq = [(x[0], x[1], x[2], 24) for x in list(itertools.product(p, d, q))]
        
        
        a, b = find_lin_coef(train[train.sat_id == sat_id], colu)
        if tune:
            AIC = 999999
            best_param = ()
            best_seas = ()

            for param in pdq:
                for param_seasonal in seasonal_pdq:
                    try:
                        mod = sm.tsa.statespace.SARIMAX(y,
                                                        order=param,
                                                        seasonal_order=param_seasonal,
                                                        enforce_stationarity=False,
                                                        enforce_invertibility=False
                                                       #exog = y_sim
                                           
                                                       )

                        results = mod.fit()



                        if AIC > results.aic:
                            #print(AIC, results.aic)
                            best_param = param
                            best_seas = param_seasonal
                            AIC = results.aic
                        print('ARIMA{}x{}12 - AIC:{}'.format(param, param_seasonal, results.aic 
                                                                           ))   
                        #print('BEST{}x{}12 - AIC:{}'.format( best_param, best_seas, AIC
                            #                                               ))    




                    except Exception as e:
                        print(e)
                        continue
            print("Best AIC: {0} \n Best param: {1} \n  Best param_seasonal: {2} \n ".format(best_param, best_seas, AIC))




        try: 
            if tune:
                mod = sm.tsa.statespace.SARIMAX(y,
                                    order=best_param,
                                    seasonal_order=best_seas,
                                    enforce_stationarity=False,
                                    enforce_invertibility=False
                                                       #exog = y_sim
                                                       )
            else:
                mod = sm.tsa.statespace.SARIMAX(y,
                                    order=(1, 1, 1),
                                    seasonal_order=(1, 1, 1, 24),
                                    enforce_stationarity=False,
                                    enforce_invertibility=False
                                                       #exog = y_sim
                                                      )

            results = mod.fit()
            
            print("AIC: {0} ".format(results.aic))
            print(type(results.aic))
            if   math.isnan(results.aic):

                AIC = 999999
                best_param = ()
                best_seas = ()

                for param in pdq:
                    for param_seasonal in seasonal_pdq:
                        try:
                            mod = sm.tsa.statespace.SARIMAX(y,
                                                            order=param,
                                                            seasonal_order=param_seasonal,
                                                            enforce_stationarity=False,
                                                            enforce_invertibility=False
                                                           #exog = y_sim,
                                                       #exog = y_sim
                                                   
                                                           )

                            results = mod.fit()



                            if AIC > results.aic:
                                #print(AIC, results.aic)
                                best_param = param
                                best_seas = param_seasonal
                                AIC = results.aic
                            print('ARIMA{}x{}12 - AIC:{}'.format(param, param_seasonal, results.aic 
                                                                               ))   
                            #print('BEST{}x{}12 - AIC:{}'.format( best_param, best_seas, AIC
                                #                                               ))    




                        except Exception as e:
                            print(e)
                            continue
                try:
                    mod = sm.tsa.statespace.SARIMAX(y,
                                    order=best_param,
                                    seasonal_order=best_seas,
                                    enforce_stationarity=False,
                                    enforce_invertibility=False
                                                       #exog = y_sim
                                                   )
                
                    results = mod.fit()
                except:
                    
                    mod = sm.tsa.statespace.SARIMAX(y,
                                    order=best_param,
                                    seasonal_order=best_seas,
                                    enforce_stationarity=False,
                                    enforce_invertibility=False,
                                                   simple_differencing=True
                                                       #exog = y_sim
                                                    )
                
                    results = mod.fit()

                
                
                
        #results.save('./models/model_save_sarimax_{}_{}.p'.format(sat_id, colu ))


            #print('ARIMA - AIC:{}'.format(results.aic  ))
            if sat_id in test_and_train:
                test.loc[test.sat_id == sat_id, colu] = results.predict(start = len(y), end=len(y)+len(y_test)-1).tolist()
            else:
                print(len(y), len(y)+len(y_test)-1)
                test_sec.loc[test_sec.sat_id == sat_id, colu] = results.predict(start = len(y), end=len(y)+len(y_test)-1).tolist()
        except Exception as e:
            print(e)
            if sat_id in test_and_train:
                test.loc[test.sat_id == sat_id, colu] = test.loc[test.sat_id == sat_id, "{0}_sim".format(colu)]
            else:
                #print(len(y), len(y)+len(y_test)-1)
                test_sec.loc[test_sec.sat_id == sat_id, colu] = test_sec.loc[test_sec.sat_id == sat_id, "{0}_sim".format(colu)]
    if colu == 'Vz':
        
        test.to_csv("part_backup_first.csv", index=False)
        test_sec.to_csv("part_backup_second.csv", index=False)
    return test, test_sec


In [53]:
def diffdates(d2):

    d1 = "2014-01-01 00:00:00.000"
    return (time.mktime(time.strptime(d2,"%Y-%m-%d %H:%M:%S.%f")) -
               time.mktime(time.strptime(d1, "%Y-%m-%d %H:%M:%S.%f")))

In [54]:
# train['diff_second_1th_january'] = train['epoch'].apply(lambda x: diffdates(x) )
# test['diff_second_1th_january'] = test['epoch'].apply(lambda x: diffdates(x) )

In [55]:
train['epoch'] = train['epoch'].apply(lambda x: datetime.datetime.strptime(x, '%Y-%m-%d %H:%M:%S.%f'))
test['epoch'] = test['epoch'].apply(lambda x: datetime.datetime.strptime(x, '%Y-%m-%dT%H:%M:%S.%f'))

In [56]:
train[train.sat_id==1].shape

(2106, 20)

In [57]:
train[train.sat_id==1].tail()

Unnamed: 0    id                   epoch  sat_id             x  \
3057        3057  3057 2014-01-31 22:15:45.938       1 -33092.618399   
3058        3058  3058 2014-01-31 22:36:57.783       1 -32678.193673   
3059        3059  3059 2014-01-31 22:58:09.628       1 -31665.342406   
3060        3060  3060 2014-01-31 23:19:21.473       1 -30034.378237   
3061        3061  3061 2014-01-31 23:40:33.318       1 -27756.260690   

                y            z        Vx        Vy        Vz         x_sim  \
3057  -281.511542 -1582.378975  0.094088 -1.839427  1.337545 -29406.078919   
3058 -2611.293944   127.879530  0.559090 -1.818598  1.347891 -27882.742274   
3059 -4892.533056  1835.695504  1.036204 -1.762460  1.333303 -25577.429154   
3060 -7077.220106  3507.336506  1.532305 -1.665557  1.290191 -22432.558095   
3061 -9107.885238  5102.708242  2.055278 -1.518181  1.211938 -18382.812351   

             y_sim        z_sim    Vx_sim    Vy_sim    Vz_sim  epoch_year  \
3057  -2719.769909 -1476.299104  0.903445 -2.329687  1.355335        2014   
3058  -5634.903507   259.572177  1.498239 -2.242285  1.367602        2014   
3059  -8389.868466  1986.924648  2.134397 -2.074305  1.340251        2014   
3060 -10865.836350  3646.968029  2.819524 -1.797623  1.258773        2014   
3061 -12896.945935  5156.151522  3.557107 -1.364583  1.097643        2014   

      epoch_month  epoch_day  epoch_hour  
3057            1         31          22  
3058            1         31          22  
3059            1         31          22  
3060            1         31          23  
3061            1         31          23

In [58]:
test[test.sat_id==1].head()

id  sat_id                   epoch         x_sim         y_sim  \
0  3927       1 2014-02-01 00:01:45.162 -13366.891347 -14236.753503   
1  3928       1 2014-02-01 00:22:57.007  -7370.434039 -14498.771520   
2  3929       1 2014-02-01 00:44:08.852   -572.068654 -13065.289498   
3  3930       1 2014-02-01 01:05:20.697   6208.945257  -9076.852425   
4  3931       1 2014-02-01 01:26:32.542  10768.200284  -2199.706707   

         z_sim    Vx_sim    Vy_sim    Vz_sim     x     y     z    Vx    Vy  \
0  6386.774555  4.333815 -0.692764  0.810774  None  None  None  None  None   
1  7130.411325  5.077413  0.360609  0.313402  None  None  None  None  None   
2  7033.794876  5.519106  2.012830 -0.539412  None  None  None  None  None   
3  5548.296900  4.849212  4.338955 -1.869600  None  None  None  None  None   
4  2272.014862  1.940505  6.192887 -3.167724  None  None  None  None  None   

     Vz  
0  None  
1  None  
2  None  
3  None  
4  None

In [59]:
test_and_train = list(set(list(test.sat_id)) & set(list(train.sat_id)) )

In [60]:
def compute_period(sat_id):
    sub_df = train[train['sat_id'] == sat_id].reset_index()
    delta_time = sub_df['epoch'][1] - sub_df['epoch'][0]
    #print(delta_time, sub_df['epoch'][2] - sub_df['epoch'][1])
    return delta_time

def get_last_date(df, sat_id):
    sub_df = df[df['sat_id'] == sat_id]
    sub_df = sub_df.sort_values(by = ['epoch'], ascending=False).reset_index()
    return sub_df['epoch'][0]
    
def compute_steps():
    df_steps = pd.DataFrame(columns = ['sat_id', 'delta_time', 'begin_date', 'end_date', 'steps'])
    for sat_id in train['sat_id'].unique():
        if sat_id in test['sat_id'].unique():
            end_date = get_last_date(test, sat_id)
        else:
            end_date = datetime.datetime(2014, 2, 28, 23, 59, 59)
        steps = 0
        delta_time = compute_period(sat_id)
        last_date = get_last_date(train, sat_id)
        begin_date = last_date
        while end_date > last_date:
            last_date += delta_time
            steps += 1
        steps +=15
        df_steps = df_steps.append({'sat_id':sat_id, 'delta_time':delta_time, 'begin_date':begin_date,
                                    'end_date': end_date,'steps':steps}, ignore_index=True)
    return df_steps

In [61]:
df_steps = compute_steps()

In [62]:
df_steps.to_excel("steps1.xlsx")

In [63]:
sizes = df_steps.steps.tolist()



In [64]:
def create_test_sec_st(test_and_train, sizes):
    
    ids =[] 
    sat_id =[]
    x = [] 
    y =[] 
    z = []
    Vx = [] 
    Vy = [] 
    Vz = []
    
    for i in range(600):
        
        if i not in  test_and_train:
            sat_id.extend([i] * sizes[i])
            x.extend([0] * sizes[i])
            y.extend([0] * sizes[i])
            z.extend([0] * sizes[i])
            Vx.extend([0] * sizes[i])
            Vy.extend([0] * sizes[i])
            Vz.extend([0] * sizes[i])
            
    d = {'sat_id': sat_id, 
         'x': x,
         'y': y,
         'z': z,
         'Vx': Vx,
         'Vy': Vy,
         'Vz': Vz,
 
        }
    
    test_sec = pd.DataFrame(data=d)
    #test_sec['id'] = test_sec.index
    
    return test_sec



In [65]:
test_sec = create_test_sec_st(test_and_train, sizes)

In [66]:
#test_sec[]

In [67]:


# for i in range(10, len(test_and_train)):
#     print("Current number: {0} \n Current ID: {1} \n Done: {2} %".format(i, test_and_train[i], i/len(test_and_train)))
#     interpolation_and_extrapolation_fitting(train, test, test_and_train[i], 'x', 0.2)
#     interpolation_and_extrapolation_fitting(train, test, test_and_train[i], 'y', 0.2)
#     interpolation_and_extrapolation_fitting(train, test, test_and_train[i], 'z', 0.2)
#     interpolation_and_extrapolation_fitting(train, test, test_and_train[i], 'Vx', 0.2)
#     interpolation_and_extrapolation_fitting(train, test, test_and_train[i], 'Vy', 0.2)
#     interpolation_and_extrapolation_fitting(train, test, test_and_train[i], 'Vz', 0.2)

In [68]:
sizes

[879,
 1915,
 388,
 331,
 1099,
 3204,
 394,
 226,
 2344,
 313,
 1609,
 1861,
 283,
 969,
 746,
 2651,
 191,
 671,
 1393,
 453,
 187,
 638,
 252,
 240,
 466,
 689,
 130,
 984,
 426,
 437,
 1073,
 304,
 288,
 1079,
 987,
 296,
 2394,
 1976,
 732,
 509,
 1051,
 1777,
 752,
 425,
 3200,
 318,
 260,
 1104,
 920,
 1285,
 1094,
 1303,
 397,
 2230,
 2230,
 719,
 301,
 1136,
 463,
 2340,
 3887,
 215,
 417,
 1311,
 223,
 565,
 191,
 725,
 2607,
 392,
 193,
 1290,
 553,
 630,
 802,
 832,
 352,
 363,
 344,
 530,
 2184,
 2104,
 282,
 542,
 591,
 993,
 1022,
 361,
 409,
 474,
 587,
 636,
 222,
 1033,
 1312,
 362,
 327,
 1104,
 410,
 1109,
 423,
 527,
 636,
 564,
 560,
 385,
 235,
 312,
 1496,
 587,
 296,
 1368,
 1039,
 329,
 741,
 822,
 560,
 253,
 739,
 747,
 237,
 1133,
 581,
 1368,
 1808,
 947,
 532,
 2005,
 286,
 416,
 611,
 463,
 476,
 587,
 706,
 2516,
 3168,
 682,
 1784,
 710,
 365,
 2439,
 1315,
 457,
 562,
 1731,
 728,
 674,
 2070,
 940,
 598,
 579,
 798,
 149,
 278,
 355,
 2469,
 876,
 32

In [ ]:
import math
from sklearn.linear_model import LinearRegression

#for i in range(0,600):
for i in range(0,600):

    test, test_sec = interpolation_and_extrapolation_test(train, test, test_sec, i, sizes, test_and_train, 'x', 'Vx', 'Vx_sim',False)
    test, test_sec = interpolation_and_extrapolation_test(train, test, test_sec, i, sizes, test_and_train, 'y', 'Vy','Vy_sim',False)
    test, test_sec = interpolation_and_extrapolation_test(train, test, test_sec, i, sizes, test_and_train, 'z', 'Vz', 'Vz_sim',False)
    test, test_sec = interpolation_and_extrapolation_test(train, test, test_sec, i, sizes, test_and_train, 'Vx', 'Vx', 'Vx_sim',False)
    test, test_sec = interpolation_and_extrapolation_test(train, test, test_sec, i, sizes, test_and_train, 'Vy', 'Vy','Vy_sim',False)
    test, test_sec = interpolation_and_extrapolation_test(train, test, test_sec, i, sizes, test_and_train, 'Vz', 'Vz', 'Vz_sim',False)
    #smape(satellite_predicted_values, satellite_true_values)

# ARIMA(0, 0, 0)x(0, 0, 0, 24)12 - AIC:54379.80481128669
# ARIMA(0, 0, 0)x(0, 0, 1, 24)12 - AIC:38513.53074606579

Current number: 450 
 Done: 0.7512520868113522 %
Current number: 451 
 Done: 0.7529215358931552 %
count
AIC: 3621.851297527089 
<class 'numpy.float64'>
542 1046
count
AIC: 3652.451979080429 
<class 'numpy.float64'>
542 1046
count
AIC: 3439.085590797554 
<class 'numpy.float64'>
542 1046
count
AIC: -3569.214816010639 
<class 'numpy.float64'>
542 1046
count
AIC: -3810.6883591507776 
<class 'numpy.float64'>
542 1046
count
AIC: -3550.6867141747275 
<class 'numpy.float64'>
542 1046
Current number: 452 
 Done: 0.7545909849749582 %
Current number: 453 
 Done: 0.7562604340567612 %
count
maxlag should be < nobs
'x_sim'
ERSTE
Current number: 454 
 Done: 0.7579298831385642 %
Current number: 455 
 Done: 0.7595993322203672 %
Current number: 456 
 Done: 0.7612687813021702 %
Current number: 457 
 Done: 0.7629382303839732 %
Current number: 458 
 Done: 0.7646076794657763 %
count
AIC: -9617.352727241121 
<class 'numpy.float64'>
2924 5581
count
AIC: -12823.664376779801 
<class 'numpy.float64'>
2924 5581
c

In [ ]:
# for i in train[train.sat_id ==570]['Vz'].tolist():
#     print(i)

In [ ]:
test_and_train

In [ ]:
test.sat_id.unique()

In [ ]:
test_sec.sat_id.unique()

In [ ]:
test[test.sat_id==252].shape

In [ ]:
test_and_train

In [ ]:
colu_real = ['x', 	'y', 	'z' ,	'Vx', 	'Vy', 	'Vz']

colu_sim = ['x_sim', 	'y_sim', 	'z_sim', 	'Vx_sim', 	'Vy_sim', 	'Vz_sim']
for i in range(len(colu_real)):
    test.loc[test.sat_id == 252, colu_real[i]] = test[test.sat_id == 252][colu_sim[i]].tolist()

In [ ]:
submission = test[["id", "x", "y", "z", "Vx", "Vy", "Vz"]]
#submission.columns = ["id", "x", "y", "z", "Vx", "Vy", "Vz"]
#submission.to_csv("submission.csv", index=False)


In [ ]:
submission.tail()

In [ ]:
# from math import sqrt
# from joblib import Parallel, delayed
# def producer():
#        for i in range(6):
#             print('Produced %s' % i)
#             yield i
# out = Parallel(n_jobs=32, verbose=100, pre_dispatch='1.5*n_jobs')(
#                 delayed(sqrt)(i) for i in producer()) 

In [ ]:
test_and_train

In [ ]:
# for i in range(len(test_and_train)):
#     print("Current number: {0} \n Current ID: {1} \n Done: {2} %".format(i, test_and_train[i], i/len(test_and_train)))


In [ ]:
submission = test[["id", "x", "y", "z", "Vx", "Vy", "Vz"]]
#submission.columns = ["id", "x", "y", "z", "Vx", "Vy", "Vz"]
#submission.to_csv("submission2.csv", index=False)

In [ ]:
# test.to_csv("part57.csv", index=False)